In [1]:
import os
import logging
import struct
import random
import math
import numpy as np
import pandas as pd
import tensorflow as tf
import pydot
import pydotplus
import graphviz
import scipy
import scipy.stats as sts
import numpy.random as npr
from logging.config import dictConfig
from scipy.stats import norm
from sklearn import metrics
from keras import regularizers
from keras.layers import Dense, Activation, Input, Dropout, BatchNormalization
from keras.models import Sequential
from keras_tqdm import TQDMNotebookCallback as ktqdm
from tqdm import tqdm_notebook as tqdm
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from statsmodels.distributions.empirical_distribution import ECDF
from matplotlib import pyplot as plt
from sklearn.metrics import roc_auc_score, roc_curve
from sklearn.metrics import precision_recall_curve, average_precision_score, confusion_matrix

%matplotlib notebook

Using TensorFlow backend.


## Network Metrics Function

In [2]:
def plot_history_graph(history, index, label, name):
    """Plot the graph for the given history metrics."""
    plt.ylim(-0.01, 0.15)
    plt.xlim(-100, 5000)
    plt.plot(history.history[index], label="Training %s = %0.6f" % (label, history.history[index][-1]))
    plt.plot(history.history["val_%s"%index], label='Testing %s = %0.6f' % (label, history.history['val_%s'%index][-1]))
    plt.title("Uniform model", fontsize=15)
    plt.ylabel(label)
    plt.xlabel('epoch')
    plt.legend(loc='upper left')
    #plt.figure(figsize=(20,10))
    #plt.savefig(name)

## Custom Activation Function

In [3]:
from keras import backend as K
from keras.utils.generic_utils import get_custom_objects

beta005 = 0.05
beta02 = 0.2
beta05 = 0.5
beta1 = 1
beta3 = 3
beta10 = 10

def custom_activation(x):
    return (K.sigmoid(x * 3))

## Reproducibility

In [4]:
os.environ['PYTHONHASHSEED'] = '0'
np.random.seed(42)
random.seed(42)
tf.set_random_seed(42)

## Logging Discrete Uniform

In [5]:
step = 50
size = 10000
n = step * size
train_size = 0.70
test_size = 1 - train_size
width = np.ceil(np.log2(n)).astype(int)
predecessors = np.arange(0, n, step)
predecessors = np.array([
    (predecessors[i]) for i in range(size)
]).astype(int)
predecessors, predecessors.shape, n

(array([     0,     50,    100, ..., 499850, 499900, 499950]),
 (10000,),
 500000)

In [6]:
cumulative_predecessors = np.array([(((i / size))) for i in range(size)])

cumulative_predecessors, cumulative_predecessors.size

(array([0.000e+00, 1.000e-04, 2.000e-04, ..., 9.997e-01, 9.998e-01,
        9.999e-01]), 10000)

In [7]:
predecessors_bits = np.array([
    list(np.binary_repr(i, width)) for i in np.arange(0, n, step)
]).astype(int)
np.set_printoptions(threshold=100)
predecessors_bits, predecessors_bits.shape

(array([[0, 0, 0, ..., 0, 0, 0],
        [0, 0, 0, ..., 0, 1, 0],
        [0, 0, 0, ..., 1, 0, 0],
        ...,
        [1, 1, 1, ..., 0, 1, 0],
        [1, 1, 1, ..., 1, 0, 0],
        [1, 1, 1, ..., 1, 1, 0]]), (10000, 19))

In [8]:
## Create training + testing set
## L'idea è utilizzare una permutazione casuale per ottenere gli elementi presenti da 0 a size
rnd_ind = npr.permutation(size)
rnd_ind

array([6252, 4684, 1731, ..., 5390,  860, 7270])

In [9]:
permutated_preds, permutated_cums = predecessors[np.ndarray.tolist(rnd_ind)], cumulative_predecessors[np.ndarray.tolist(rnd_ind)]
train_ind, train_lab = permutated_preds[:int(size * 0.70)], permutated_cums[:int(size * 0.70)]
test_ind, test_lab = permutated_preds[int(size * 0.70):], permutated_cums[int(size * 0.70):]
permutated_preds, permutated_cums

(array([312600, 234200,  86550, ..., 269500,  43000, 363500]),
 array([0.6252, 0.4684, 0.1731, ..., 0.539 , 0.086 , 0.727 ]))

In [10]:
train_ind_2 = np.array([list(np.binary_repr(train_ind[i], width)) for i in range(train_ind.size)]).astype(int)
train_ind_2

array([[1, 0, 0, ..., 0, 0, 0],
       [0, 1, 1, ..., 0, 0, 0],
       [0, 0, 1, ..., 1, 1, 0],
       ...,
       [0, 1, 0, ..., 0, 1, 0],
       [0, 0, 0, ..., 1, 0, 0],
       [1, 0, 0, ..., 1, 1, 0]])

In [11]:
test_ind_2 = np.array([list(np.binary_repr(test_ind[i], width)) for i in range(test_ind.size)]).astype(int)
test_ind_2

array([[1, 0, 0, ..., 0, 1, 0],
       [0, 0, 0, ..., 1, 1, 0],
       [1, 0, 1, ..., 1, 1, 0],
       ...,
       [1, 0, 0, ..., 1, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [1, 0, 1, ..., 1, 0, 0]])

## Functions to build the model

In [12]:
def build_model(neurons):
    """ Return keras network model """
    model = Sequential()
    model.add(Dense(int(neurons * 3), input_dim=neurons, name="Input_dense_layer", activation=custom_activation))
    model.add(BatchNormalization())
    model.add(Dense(int(neurons * 2), name="Hidden_dense_layer", activation="sigmoid"))
    model.add(BatchNormalization())
    model.add(Dense(1, name="Output_dense_layer", activation="sigmoid"))
    model.compile(
        loss='mean_squared_error', 
        optimizer="adam",
        metrics=['mean_absolute_error'])

    return model

In [13]:
from keras.utils import plot_model

model_1k = build_model(width)
model_5k = build_model(width)
model_10k = build_model(width)
model_25k = build_model(width)

os.environ['PYTHONHASHSEED'] = '0'
np.random.seed(42)
random.seed(42)
tf.set_random_seed(42)

history_1k = model_1k.fit(
    train_ind_2, 
    train_lab,
    epochs=1000,
    shuffle=True,
    batch_size=256,
    verbose=0,
    callbacks=[ktqdm(metric_format="{name}: {value:e}")],
    validation_data=(test_ind_2, test_lab)
)

os.environ['PYTHONHASHSEED'] = '0'
np.random.seed(42)
random.seed(42)
tf.set_random_seed(42)

history_5k = model_5k.fit(
    train_ind_2, 
    train_lab,
    epochs=5000,
    shuffle=True,
    batch_size=256,
    verbose=0,
    callbacks=[ktqdm(metric_format="{name}: {value:e}")],
    validation_data=(test_ind_2, test_lab)
)

os.environ['PYTHONHASHSEED'] = '0'
np.random.seed(42)
random.seed(42)
tf.set_random_seed(42)

history_10k = model_10k.fit(
    train_ind_2, 
    train_lab,
    epochs=10000,
    shuffle=True,
    batch_size=256,
    verbose=0,
    callbacks=[ktqdm(metric_format="{name}: {value:e}")],
    validation_data=(test_ind_2, test_lab)
)

In [ ]:
os.environ['PYTHONHASHSEED'] = '0'
np.random.seed(42)
random.seed(42)
tf.set_random_seed(42)

history_25k = model_25k.fit(
    train_ind_2, 
    train_lab,
    epochs=25000,
    shuffle=True,
    batch_size=256,
    verbose=0,
    callbacks=[ktqdm(metric_format="{name}: {value:e}")],
    validation_data=(test_ind_2, test_lab)
)

%matplotlib notebook
plot_history_graph(history_1k, 'mean_absolute_error', 'mae', "31_mae_uniform.png")

%matplotlib notebook
plot_history_graph(history_1k, 'loss', 'loss', "31_mse_uniform")

%matplotlib notebook
plot_history_graph(history_5k, 'mean_absolute_error', 'mae', "32_mae_uniform.png")

%matplotlib notebook
plot_history_graph(history_5k, 'loss', 'loss', "32_mse_uniform")

%matplotlib notebook
plot_history_graph(history_10k, 'mean_absolute_error', 'mae', "33_mae_uniform.png")

%matplotlib notebook
plot_history_graph(history_10k, 'loss', 'loss', "33_mse_uniform")

In [ ]:
%matplotlib notebook
plot_history_graph(history_25k, 'mean_absolute_error', 'mae', "Final_mae_uniform.png")

In [ ]:
%matplotlib notebook
plot_history_graph(history_25k, 'loss', 'loss', "Final_mse_uniform.png")

## Boxplot error

In [ ]:
def prediction(num, width, model, size):
    bin = np.array([list(np.binary_repr(num, width))])
    #print("Prediction on ", num, ":\t ", model.predict(bin))
    return int(np.reshape(np.ceil(model.predict(bin) * size), 1)[0])

In [ ]:
def mae_errors(model, size, step, width, predecessors, rnd_ind):
    errors = []
    ## L'operazione è ripetuta size volte
    for x in range(size):
        ## L'indice che mi aspetto è in posizione x di rnd_ind
        expected_index = rnd_ind[x]
        print(x)
        ## Ripeto la predizione step volte
        for i in range(step):
            ## Predico predecessors[expected_index] + i
            predicted_index = prediction(predecessors[expected_index] + i, width, model, size)
            ## Calcolo la distanza tra l'indice ottenuto e l'indice atteso
            errors.append(abs(expected_index - predicted_index))
    ## Plot degli errori
    return errors

In [ ]:
#errors_1k = mae_errors(model_1k, size, step, width, predecessors, rnd_ind)

In [ ]:
#errors_5k = mae_errors(model_5k, size, step, width, predecessors, rnd_ind)

In [ ]:
#errors_10k = mae_errors(model_10k, size, step, width, predecessors, rnd_ind)

In [ ]:
errors_25k = mae_errors(model_25k, size, step, width, predecessors, rnd_ind)

%matplotlib notebook
plt.boxplot(errors_1k)
plt.savefig("31_mae_boxplot.png")
plt.show()

np.median(errors_1k), np.mean(errors_1k)

%matplotlib notebook
plt.boxplot(errors_5k)
plt.savefig("32_mae_boxplot.png")
plt.show()

np.median(errors_5k), np.mean(errors_5k)

%matplotlib notebook
plt.boxplot(errors_10k)
plt.savefig("33_mae_boxplot.png")
plt.show()

np.median(errors_10k), np.mean(errors_10k)

In [ ]:
%matplotlib inline
plt.ylim(0, 250)
plt.title("Uniform model errors", fontsize=15)
plt.boxplot(errors_25k)
#plt.show()
plt.savefig("Final_boxplot_uniform")

In [ ]:
log = open("log_2.txt", "a")
"""log.writelines(("1000 Epochs:\n",
                "\t31_mae_uniform.png\n",
                "\t31_mse_uniform.png\n",
                "\t31_mae_boxplot.png\n",
                "\tMediana:\t", str(np.median(errors_1k)), "\n",
                "\tMedia:\t\t", str(np.mean(errors_1k)),"\n\n"))
log.writelines(("5000 Epochs\n",
                "\t32_mae_uniform.png\n",
                "\t32_mse_uniform.png\n",
                "\t32_mae_boxplot.png\n",
                "\tMediana:\t", str(np.median(errors_5k)), "\n",
                "\tMedia:\t\t", str(np.mean(errors_5k)), "\n\n"))"""
"""log.writelines(("10000 Epochs\n",
                "\t33_mae_uniform.png\n",
                "\t33_mse_uniform.png\n",
                "\t33_mae_boxplot.png\n",
                "\tMediana:\t", str(np.median(errors_10k)), "\n",
                "\tMedia:\t\t", str(np.mean(errors_10k)), "\n\n"))"""
"""log.writelines(("25000 Epochs\n",
                "\t34_mae_uniform.png\n",
                "\t34_mse_uniform.png\n",
                "\t34_mae_boxplot.png\n",
                "\tMediana:\t", str(np.median(errors_25k)), "\n",
                "\tMedia:\t\t", str(np.mean(errors_25k)), "\n\n"))"""
log.close()

In [ ]:
#import h5py
#model_25k.save("Model_discrete_uniform_25k.h5")

In [ ]:
#predicts = model_25k.predict(test_ind_2)
#from keras import models
#new_mod = models.load_model("Model_discrete_uniform_25k.h5", custom_objects={'custom_activation':custom_activation})
#new_predicts = new_mod.predict(test_ind_2)


In [ ]:
#np.testing.assert_allclose(predicts, new_predicts, atol=1e-6)